In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.stats.diagnostic import acorr_ljungbox
from sklearn.ensemble import RandomForestRegressor
from scipy.stats import skew, kurtosis, variation
import lightgbm as lgb
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error, r2_score

In [2]:
sns.set_style("whitegrid")
plt.rcParams['figure.figsize'] = (15, 7)

In [3]:
# Sabitler
COLS = ['id', 'cycle', 'setting1', 'setting2', 'setting3'] + [f's{i}' for i in range(1, 22)]
# Gürültü analizi için kullanılacak, anlamlı sensörler
TARGET_SENSORS = ['s2', 's3', 's4', 's7', 's8', 's9', 's11', 's12', 's13', 's14', 's15', 's17', 's20', 's21']
BASELINE_PERCENTAGE = 0.20 # İlk %20'lik dilim 'Normal Çalışma' periyodu
ROLLING_WINDOW = 50 # Kayar pencere boyutu

In [4]:
# 1. Veri Yükleme ve RUL Hesaplama Fonksiyonu
def load_and_preprocess_data(file_path):
    """Veriyi yükler, RUL hesaplar ve motor bazında z-score normalizasyonu yapar."""
    try:
        df = pd.read_csv(file_path, sep='\s+', header=None, names=COLS, index_col=False)
    except FileNotFoundError:
        print(f"HATA: '{file_path}' dosyası bulunamadı.")
        return pd.DataFrame()

    # RUL Hesaplama (Her motorun maksimum döngüsü bulunur ve mevcut döngüden çıkarılarak RUL elde edilir)
    # NOT: CMAPSS test verisi için bu RUL hesaplaması, harici bir "RUL_FD001.txt" dosyasından
    # elde edilen gerçek RUL değerleri ile birleştirilerek yapılmalıdır. 
    # Ancak orijinal kodunuzdaki RUL hesaplama mantığını koruyorum.
    max_cycles = df.groupby('id')['cycle'].max()
    df['RUL'] = df.apply(lambda row: max_cycles[row['id']] - row['cycle'], axis=1)

    # Motor Bazında Z-Score Normalizasyonu (Orijinal Kodun Mantığı Korunmuştur)
    def normalize_by_id(group):
        for sensor in TARGET_SENSORS:
            group[f'norm_{sensor}'] = StandardScaler().fit_transform(group[[sensor]])
        return group

    df = df.groupby('id', group_keys=False).apply(normalize_by_id)
    return df


In [5]:
def extract_residual_component(df, sensor):
    """Belirtilen sensör için gürültü (residual) bileşenini ARIMA ile ayırır."""
    df[f'residual_{sensor}'] = np.nan
    
    # Her motor için ayrı ayrı residual hesabı
    for engine_id in df['id'].unique():
        engine_data = df[df['id'] == engine_id].copy()
        
        # Trend'i yakalamak için basit bir ARIMA(1, 1, 0) modeli uygula
        try:
            model = ARIMA(engine_data[f'norm_{sensor}'], order=(1, 1, 0), trend='t', enforce_stationarity=False)
            model_fit = model.fit(disp=False)
            df.loc[engine_data.index, f'residual_{sensor}'] = model_fit.resid
            
        except Exception:
            # ARIMA hata verirse basitçe hareketli ortalama farkını al
            window = 5
            ma = engine_data[f'norm_{sensor}'].rolling(window=window, min_periods=1).mean()
            df.loc[engine_data.index, f'residual_{sensor}'] = engine_data[f'norm_{sensor}'] - ma
    
    return df


In [6]:
# 3. NII (Noise Instability Index) Metrikleri için Baseline Varyansını Hesaplama (FIT)
def fit_baseline_vars(df_train):
    """Tüm sensörler için eğitim setinden Baseline Varyanslarını hesaplar."""
    print("2.1. ⚙️ Eğitim Verisinden Baseline Varyansları (NII için) Hesaplanıyor...")
    baseline_vars = {}
    engine_ids = df_train['id'].unique()
    
    for sensor in TARGET_SENSORS:
        res_col = f'residual_{sensor}'
        for engine_id in engine_ids:
            engine_data = df_train[df_train['id'] == engine_id]
            max_cycle = engine_data['cycle'].max()
            baseline_limit = int(max_cycle * BASELINE_PERCENTAGE)
            
            # Baseline Residual Varyansı Hesapla (σ_0^2)
            baseline_resid = engine_data[engine_data['cycle'] <= baseline_limit][res_col].dropna()
            
            # (id, sensor) tuple'ı ile varyansı sakla
            baseline_vars[(engine_id, sensor)] = baseline_resid.var() + 1e-6 # Hata önlemek için epsilon
    
    print("2.2. ✅ Baseline Varyansları Tamamlandı.")
    return baseline_vars


In [7]:
# 4. NII Metriklerini Hesaplama (TRANSFORM)
def calculate_nii(df, baseline_vars):
    """Verilen veri seti ve baseline varyanslarını kullanarak NII metriklerini hesaplar."""
    df['NII_Combined'] = 0.0 # Birleşik NII skoru
    
    for sensor in TARGET_SENSORS:
        res_col = f'residual_{sensor}'
        nii_col = f'NII_{sensor}'
        
        # Kayar Pencere Varyansı Hesapla (σ_t^2)
        df[f'rolling_var_{sensor}'] = df.groupby('id')[res_col].rolling(
            window=ROLLING_WINDOW, min_periods=1
        ).var().reset_index(level=0, drop=True)
        
        # NII = (Kayar Varyans) / (Baseline Varyans)
        df[nii_col] = df.apply(
            lambda row: row[f'rolling_var_{sensor}'] / baseline_vars.get((row['id'], sensor), 1), 
            axis=1
        )
        
        # NII Kombinasyonuna Ekle
        df['NII_Combined'] += df[nii_col]

    # NII Ortalaması
    df['NII_Combined'] /= len(TARGET_SENSORS)
    
    return df


In [8]:
# 5. Kayar İstatistiksel Öznitelikleri Hesaplama Fonksiyonu
def extract_statistical_features(df):
    """Residual ve NII_Combined üzerinde kayar istatistiksel öznitelikler hesaplar."""
    print("3. ⚙️ Kayar İstatistiksel Öznitelikler Hesaplanıyor...")
    
    new_cols = []
    
    # Residual Component'in (Gürültü) İstatistiksel Öznitelikleri
    for sensor in TARGET_SENSORS:
        res_col = f'residual_{sensor}'
        
        # Kayar Pencere (ROLLING_WINDOW) üzerinde istatistiksel öznitelik hesapla
        rolling_mean = df.groupby('id')[res_col].rolling(window=ROLLING_WINDOW, min_periods=1).mean()
        rolling_std = df.groupby('id')[res_col].rolling(window=ROLLING_WINDOW, min_periods=1).std()
        rolling_skew = df.groupby('id')[res_col].rolling(window=ROLLING_WINDOW, min_periods=1).apply(skew, raw=True)
        rolling_kurt = df.groupby('id')[res_col].rolling(window=ROLLING_WINDOW, min_periods=1).apply(kurtosis, raw=True)
        
        # DataFrame'e ekle
        df[f'{sensor}_res_mean'] = rolling_mean.reset_index(level=0, drop=True)
        df[f'{sensor}_res_std'] = rolling_std.reset_index(level=0, drop=True)
        df[f'{sensor}_res_skew'] = rolling_skew.reset_index(level=0, drop=True)
        df[f'{sensor}_res_kurt'] = rolling_kurt.reset_index(level=0, drop=True)
        
        new_cols.extend([f'{sensor}_res_mean', f'{sensor}_res_std', f'{sensor}_res_skew', f'{sensor}_res_kurt'])

    # NII_Combined üzerinde Kayar İstatistiksel Öznitelikler
    rolling_mean_nii = df.groupby('id')['NII_Combined'].rolling(window=ROLLING_WINDOW, min_periods=1).mean()
    rolling_std_nii = df.groupby('id')['NII_Combined'].rolling(window=ROLLING_WINDOW, min_periods=1).std()
    
    df['NII_Combined_mean'] = rolling_mean_nii.reset_index(level=0, drop=True)
    df['NII_Combined_std'] = rolling_std_nii.reset_index(level=0, drop=True)
    
    new_cols.extend(['NII_Combined_mean', 'NII_Combined_std'])

    print("4. ✅ Kayar İstatistiksel Öznitelikler Hesaplandı.")
    return df, new_cols


In [10]:
# 1. Eğitim Verisini Yükle ve Ön İşle
df_train = load_and_preprocess_data('CMAPSSData/train_FD001.txt')
if df_train.empty:
    raise SystemExit("Eğitim verisi yüklenemedi.")


c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future ver

In [11]:
# 2. Feature Engineering - Residual Bileşenlerini Hesapla
for sensor in TARGET_SENSORS:
    df_train = extract_residual_component(df_train, sensor)


c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueW

In [12]:
# 3. Feature Engineering - NII Baseline'ı Oluştur (Sadece Eğitim Seti Üzerinden)
baseline_vars = fit_baseline_vars(df_train)
df_train = calculate_nii(df_train, baseline_vars)
print("5. ✅ NII Metrikleri Eğitim Seti İçin Tamamlandı.")


2.1. ⚙️ Eğitim Verisinden Baseline Varyansları (NII için) Hesaplanıyor...
2.2. ✅ Baseline Varyansları Tamamlandı.
5. ✅ NII Metrikleri Eğitim Seti İçin Tamamlandı.


In [13]:
# 4. Feature Engineering - Kayar İstatistiksel Öznitelikleri Hesapla
df_train, stat_features = extract_statistical_features(df_train)


3. ⚙️ Kayar İstatistiksel Öznitelikler Hesaplanıyor...


C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:21: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_skew'] = rolling_skew.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:22: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_kurt'] = rolling_kurt.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fr

4. ✅ Kayar İstatistiksel Öznitelikler Hesaplandı.


C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_mean'] = rolling_mean.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_std'] = rolling_std.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:21: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fram

In [14]:
# 5. Öznitelik Listesini Tanımla
NORM_COLS = [f'norm_{s}' for s in TARGET_SENSORS]
RESIDUAL_COLS = [f'residual_{s}' for s in TARGET_SENSORS]
NII_COLS = [f'NII_{s}' for s in TARGET_SENSORS]
FEATURES = NORM_COLS + RESIDUAL_COLS + NII_COLS + ['NII_Combined'] + stat_features


In [15]:
# 6. Eğitim Setini Hazırla
# İlk birkaç döngüde kayar pencere ve residual hesaplamalarından ötürü NaN değerler oluşabilir, 
# bu satırları düşürerek eğitim kümesini oluştur.
X_train = df_train[FEATURES].dropna()
y_train = df_train.loc[X_train.index, 'RUL']

In [16]:
print(f"\n✅ Eğitim Verisi Hazır: {len(X_train)} örnek.")
print(f"Kullanılan Toplam Öznitelik Sayısı: {len(FEATURES)}")



✅ Eğitim Verisi Hazır: 20410 örnek.
Kullanılan Toplam Öznitelik Sayısı: 101


In [17]:
df_test = load_and_preprocess_data('CMAPSSData/test_FD001.txt')
if df_test.empty:
    raise SystemExit("Test verisi yüklenemedi.")


c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future ver

In [18]:
# 2. Feature Engineering - Residual Bileşenlerini Hesapla
for sensor in TARGET_SENSORS:
    df_test = extract_residual_component(df_test, sensor)


c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueW

In [19]:
# 3. Feature Engineering - NII Metriklerini Hesapla (Eğitimden Gelen Baseline'ı Kullan)
df_test = calculate_nii(df_test, baseline_vars)
print("6. ✅ NII Metrikleri Test Seti İçin Tamamlandı (Eğitim Baseline'ı Kullanıldı).")


6. ✅ NII Metrikleri Test Seti İçin Tamamlandı (Eğitim Baseline'ı Kullanıldı).


In [20]:
# 4. Feature Engineering - Kayar İstatistiksel Öznitelikleri Hesapla
df_test, _ = extract_statistical_features(df_test)


3. ⚙️ Kayar İstatistiksel Öznitelikler Hesaplanıyor...


C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:21: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_skew'] = rolling_skew.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:22: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_kurt'] = rolling_kurt.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fr

4. ✅ Kayar İstatistiksel Öznitelikler Hesaplandı.


C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_mean'] = rolling_mean.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{sensor}_res_std'] = rolling_std.reset_index(level=0, drop=True)
C:\Users\tlgcl\AppData\Local\Temp\ipykernel_71488\3005264069.py:21: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fram

In [21]:
# 5. Test Setini Hazırla
# Eğitim setinde olduğu gibi NaN değerleri düşür.
X_test = df_test[FEATURES].dropna()
y_test = df_test.loc[X_test.index, 'RUL']

In [22]:
print(f"\n✅ Test Verisi Hazır: {len(X_test)} örnek.")


✅ Test Verisi Hazır: 12874 örnek.


In [23]:
# Grid Search için Parametre Alanı
param_grid = {
    'n_estimators': [100, 200],
    'max_depth': [6, 10]
}

In [24]:
# Modeli ve Grid Search'ü tanımla
rf_model = RandomForestRegressor(random_state=42, n_jobs=-1)
gscv_rf = GridSearchCV(estimator=rf_model, param_grid=param_grid, cv=3, 
                       scoring='neg_mean_squared_error', verbose=1)


In [25]:
# Modeli Eğitim Verisi ile Eğit
gscv_rf.fit(X_train, y_train)

Fitting 3 folds for each of 4 candidates, totalling 12 fits


c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future ver

GridSearchCV(cv=3, estimator=RandomForestRegressor(n_jobs=-1, random_state=42),
             param_grid={'max_depth': [6, 10], 'n_estimators': [100, 200]},
             scoring='neg_mean_squared_error', verbose=1)

In [26]:
print("\n7. ✅ Model Eğitimi Tamamlandı.")
print(f"En İyi Parametreler: {gscv_rf.best_params_}")
print(f"En İyi MSE Skoru (Cross-Validation): {-gscv_rf.best_score_:.2f}")



7. ✅ Model Eğitimi Tamamlandı.
En İyi Parametreler: {'max_depth': 10, 'n_estimators': 100}
En İyi MSE Skoru (Cross-Validation): 1282.33


In [27]:
# --- MODEL DEĞERLENDİRMESİ (Test Verisi Üzerinde) ---

print("\n--- MODEL DEĞERLENDİRMESİ BAŞLIYOR (Test Verisi) ---")



--- MODEL DEĞERLENDİRMESİ BAŞLIYOR (Test Verisi) ---


In [28]:
# Test seti üzerinde tahmin yap
y_pred_test = gscv_rf.predict(X_test)

c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):


In [29]:
# Metrikleri hesapla
rmse_test = np.sqrt(mean_squared_error(y_test, y_pred_test))
r2_test = r2_score(y_test, y_pred_test)

c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\tlgcl\anaconda3\envs\workspace\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` i

In [30]:
print(f"Test Seti RMSE (Kök Ortalama Kare Hata): {rmse_test:.2f}")
print(f"Test Seti R-Kare Skoru (R2): {r2_test:.4f}")
print("8. ✅ Test Değerlendirmesi Tamamlandı.")

Test Seti RMSE (Kök Ortalama Kare Hata): 46.66
Test Seti R-Kare Skoru (R2): 0.2121
8. ✅ Test Değerlendirmesi Tamamlandı.
